# GEt NCBI cluster and blast

In [4]:
import Bio
import re
import pandas as pd
from Bio import SeqIO
from Bio.Seq import Seq
from Bio import Entrez
 
from Bio.Blast import NCBIWWW
from Bio.Blast import NCBIXML
filename_input="Output/permutationsof4+locus/bacilluspseudomonaslistpositivetestover70.fasta"
filename_output=filename_input+"info.csv"
tableofproteins=pd.DataFrame(columns=['Protein Reference','Acessiongenome','Species',"Definition","proteins","blasts","products"])
Entrez.email = "friederike@biermann-erfurt.de"
listfasta=[]
liststrains=[]


def find_between( s, first, last ):
    try:
        start = s.index( first ) + len( first )
        end = s.index( last, start )
        return s[start:end]
    except ValueError:
        return ""
def find_infrontof( s, last ):
    try:
        start = 0
        end = s.index( last, start )
        return s[start:end]
    except ValueError:
        return ""
def find_after( s, first ):
    try:
        start =s.index( first ) + len( first )
        end = len(s)
        return s[start:end]
    except ValueError:
        return ""


#actually finding in fastas
for record in SeqIO.parse(filename_input, "fasta"):
    try:
            if "ref" in record.id:
                gi=find_between(record.id, "ref|","|")
            if "gb" in record.id:
                gi=find_between(record.id, "gb|","|")           
            print (gi)
            ref=str(record.seq)
            handle = Entrez.elink(dbFrom = "protein", db = "nucleotide",id=gi)
            record = str(Entrez.read(handle))
            
            handle.close()
            listgenes=re.findall("(?<=Id': ')[0-9]+",record)

            listgenes=listgenes[:int(len(listgenes)/2)]
        
            
            for name1 in listgenes[:2]:
                dnahandle1 = Entrez.efetch(db="nucleotide", id=name1, rettype='gbwithparts',retmode="xml")
                
                record = Entrez.read(dnahandle1)
                dnahandle1.close()
                definition=str(record[0]["GBSeq_definition"])
                species = record[0]["GBSeq_organism"]
                
                listproteins=[]
                listsequences=[]
                listproducts=[]
                for match in re.finditer(ref, str(record)):
                    
                    proteinspan1=match.span()[0]
                    proteinspan2=int((proteinspan1))-25000
                    proteinspan3=int((proteinspan1))+27000
                    intervalrecord=str(record)[proteinspan2:proteinspan3]
                    print("%")
                    if "terpene" not in intervalrecord:
                        for match in re.finditer("(?<={'GBQualifier_name': 'translation', 'GBQualifier_value': ')\w+", intervalrecord):
                            listsequences.append(match.group())
                        
                        for match in re.finditer("(?<={'GBQualifier_name': 'locus_tag', 'GBQualifier_value': ')\w+", intervalrecord):
                            listproteins.append(match.group())
                        for match in re.finditer("(?<={'GBQualifier_name': 'product', 'GBQualifier_value': ')\w+", intervalrecord):
                            listproducts.append(match.group())
                            
                        
                        res = [] 
                        [res.append(x) for x in listproteins if x not in res]
                       
                        new_row={'Protein Reference':gi,'Acessiongenome':name1,'Species':species,"Definition":definition,"proteins":res,"blasts":listsequences,"products":listproducts}
                        tableofproteins = tableofproteins.append(new_row, ignore_index=True)
    except: 
        print ("a")

tableofproteins.to_csv(filename_output, index=False) 


WP_080642335.1
%
%
WP_102592936.1
%
%
WP_092249696.1
%
%
WP_057399521.1
%
WP_153871954.1
%
%
WP_153839691.1
%
WP_122582593.1
%
%
WP_130138436.1
%
WP_123478026.1
%
WP_122738961.1
%
WP_122464193.1
%
WP_116668398.1
%
WP_083218084.1
%
WP_083216655.1
%
WP_083205629.1
%
WP_071495089.1
%
%
WP_064055105.1
%
%
WP_059397318.1
%
WP_034119619.1
%
WP_104502961.1
%
WP_101220652.1
%
WP_093513798.1
%
WP_093127211.1
%
WP_092484386.1
%
WP_082781486.1
%
WP_082461536.1
%
WP_076960813.1
%
%
WP_057010874.1
%
%
WP_056847841.1
%
WP_046068191.1
%
WP_043049913.1
%
%
WP_141606426.1
%
WP_137201540.1
%
WP_095053371.1
%
WP_090404030.1
%
%
WP_068967176.1
%
ETK23155.1
%
EJM94789.1
%
WP_198858843.1
%
WP_195696143.1
%
WP_153255243.1
%
WP_191955415.1
%
WP_191952776.1
%
%
WP_191951234.1
%
%
WP_182029207.1
%
WP_181284259.1
%
WP_178952454.1
%
WP_178923447.1
%
WP_177111342.1
%
WP_177074845.1
%
WP_176343514.1
%
WP_169993658.1
%
%
WP_065890995.1
%
%
WP_161905023.1
%
WP_127881537.1
%
%
WP_124358401.1
%
WP_065873112.1
%
WP_1288

In [3]:
import re
intervalrecord="{'GBQualifier_name': 'locus_tag', 'GBQualifier_value': AH456_95038 blsojsidId': 'asfs89_gr  '"
for match in re.finditer("(?<={'GBQualifier_name': 'locus_tag', 'GBQualifier_value':)\w+", intervalrecord):
                            print(match)

# blast with fasta

In [7]:
import Bio
import re
import pandas as pd
from Bio import SeqIO
from Bio.Seq import Seq
from Bio import Entrez

#Adjust the file locations to match your own:
rpsblast_db = "/home/friederike/ncbi-blast-2.11.0+/bin/Sigma"
rpsblast_exe = "/home/friederike/ncbi-blast-2.11.0+/rpsblast.exe"

query_filename = "Fasta/terpenecyclshort.fasta"
#query_filename = "NC_003197.faa"

E_VALUE_THRESH = 0.00001 #Adjust the expectation cut-off here

from Bio.Blast.Applications import NcbirpstblastnCommandline 
cline= NcbirpstblastnCommandline(help=True)
from Bio.Blast import NCBIXML

for record in NCBIXML.parse(output_handle) :
    #We want to ignore any queries with no search results:
    if record.alignments :
        print ("QUERY: %s..." % record.query[:60])
        for align in record.alignments :
            for hsp in align.hsps :
                print (" %s HSP, e=%f, from position %i to %i"\
                % (align.hit_id, hsp.expect, hsp.query_start, hsp.query_end))
                assert hsp.expect <= E_VALUE_THRESH
print ("Done")

AttributeError: 'NcbirpstblastnCommandline' object has no attribute 'read'

# read table file and fill fastas with it

In [17]:
import Bio
import re
import pandas as pd
from Bio import SeqIO
from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord

filename_input="Output/permutationsof4+locus/allp450ncbi_strep_ecoli_positivesover60.fasta"
filename_output=filename_input+"info.csv"
folderout="Output/permutationsof4+locus/allp450ncbi_strep_ecoli_positivesover60/"
# making dataframe  
df = pd.read_csv(filename_output)  
for i in range (0,len(df)):
    fastalist=[]
    protref=df['Protein Reference'][i]
    print (protref)
    genome=df['Acessiongenome'][i]

    outfile=folderout+protref+"_"+str(genome)+".fasta"
    sequences=df['blasts'][i]
    
    sequences = sequences.strip('][').split(', ')
    proteins=df["proteins"][i]
    proteins = proteins.strip('][').split(', ')+["test"]*10
    print (proteins)
    if len(sequences)>0:
        for (index, seq) in enumerate(sequences):
            print (index)
            print (Seq(seq),proteins[index])
            fastalist.append(SeqRecord(Seq(seq),id=proteins[index]))
    
    SeqIO.write(fastalist, outfile, "fasta")

WP_003958577.1
["'GE265_RS32690'", "'GE265_RS32695'", "'GE265_RS32700'", "'GE265_RS32705'", "'GE265_RS32710'", "'GE265_RS32715'", "'GE265_RS32720'", "'GE265_RS32725'", "'GE265_RS32730'", "'GE265_RS32735'", "'GE265_RS32740'", "'GE265_RS32745'", "'GE265_RS32750'", "'GE265_RS32755'", "'GE265_RS32760'", "'GE265_RS32765'", "'GE265_RS32770'", "'GE265_RS32775'", "'GE265_RS32780'", "'GE265_RS32785'", "'GE265_RS32790'", "'GE265_RS32795'", "'GE265_RS32800'", "'GE265_RS32805'", "'GE265_RS32810'", "'GE265_RS32815'", "'GE265_RS32820'", 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test']
0
'MTPRVLHVAPKGRGAHRTITDALRAAADGDGDEIRVAPGEYGERVLLDRSVSLVADRGAGTVLLTAPEPGHPVLELSAPRAVLHGITLVGSDPGKPAAVLFSGTAELTECRISGGRIEIGGSASAVLRDTRVHRAALVGVHLTSSGPVTLDQCTIEDIEGTGVVVAGRAAAVLTGTEVRRVSGSGLRVRGEARAAFHGCGTVGAGRNGLLVEERASVLLLDCRLKDSTGDGVQVTGSSPRGDRAGDPPATADGGVLLVGCEVLRTGGDGVAVTNDADVLLRDSRIRQTTGSGVSAAEESAVEMVDCRVSGVGGSGLLAAARSRLSVRGTSVRGSAANGALAYDSSELTLVESDLMECAFTAVHVGARARAALESVRVGPTPEHGIRAT

5
'MTENTVTVREARAHLADHINRAEEGVPTVITRNGAPVAAVVPIADFEALEEAADVMLAREAEAVLAEGGPTVTMAELLADLFTEQDGEAA' 'IE229_RS13695'
6
'MKYAFRFTAAAQRQLRAISRPDAMRILTALTALGDDPYRQDADVKKLTGPSGLYRLRVGSYRVAYQINDGELVVLVVKVGDRRDVYRNL' 'IE229_RS13700'
7
'MTRVAAVDCGTNSIRLLVADAHPETGELTDLDRRMTIVRLGQGVDRTGRLAPEALERTFAACREYAAVIKEHGAERLRFVATSASRDAENRDAFVRGVLDILGVEPEVITGDQEAEFSFTGATKELTGRDDLARPYLVVDIGGGSTEFVVGEERVRAARSVDVGCVRMTERHLVTDGTVTDPPTEDRIAAMRADIEAALDLAERTVPLHEARTLVGLAGSVTTVSAIAQDLPAYDSARIHHSRVSRDRVREITEWLLRSTHAERAAVPSMHPGRVDVIGAGALVLLSIMDRIGAEEVVVSEHDILDGIGWSLA' 'IE229_RS13705'
8
'METPPPTTPRTEPTDADVEAFKQQLGRPPRGLRAIAHRCPCGSPDVVETAPRLPDGTPFPTLYYLTCPRANSAIGTLEANGVMKEMTERLATDPELAAAYRAAHEDYVRRRDEIEELKGFPSAGGMPDRVKCLHVLVAHALAAGPGVNPLGDEALAMLPEWWRKGSCVVPDRQTTTQGEAR' 'IE229_RS13710'
9
'MAVKDRDRFSTATRLRLLGEQTAARVYRSQTRRQARRSRLTSRAALLALVLCSLVVALAYPMRQYVSQRADIADLKREKQQARQRVEQLRDLKARWQDDAYAEQQIRLRLHYVMPGETGFVVVDPEAARQSRADLGAADRPWYSNVWDGVDKSDASGQKN' 'IE229_RS13715'
10
'MLVPSIDVVVAREILDSRGNPTVEVEVGLDDGSTGRAAVPSGASTGAFEAIELRDGDQ

WP_093708506.1
["'BLW14_RS19305'", "'BLW14_RS19310'", "'BLW14_RS19315'", "'BLW14_RS19320'", "'BLW14_RS19325'", "'BLW14_RS19330'", "'BLW14_RS19335'", "'BLW14_RS19340'", "'BLW14_RS19345'", "'BLW14_RS19350'", "'BLW14_RS19355'", "'BLW14_RS19360'", "'BLW14_RS19365'", "'BLW14_RS19370'", "'BLW14_RS19375'", "'BLW14_RS19380'", "'BLW14_RS19385'", "'BLW14_RS19390'", "'BLW14_RS19395'", "'BLW14_RS19400'", "'BLW14_RS19405'", "'BLW14_RS19410'", "'BLW14_RS19415'", "'BLW14_RS19420'", "'BLW14_RS19425'", "'BLW14_RS19430'", "'BLW14_RS19435'", "'BLW14_RS19440'", "'BLW14_RS19445'", "'BLW14_RS19450'", "'BLW14_RS19455'", 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test']
0
'MVSLGDSFISGEAGRWAGNSNVRANGYSGTDRAWDPATGKRDPYRVYGSSYDNGCNRSDVAEVQSVTLDLSRLNLACSGATSKAVLLPESGGKPFKGERSQAREISSVLADAADEGGAEFLDLSRSFEGREVCSTSTRQADAAHPPAGDTSEWVRFVTSGIGQGQKQESLHPNRYGQQALGTCLTLQLEQPSGDRRCTNAPGRGPATMRLNSID' 'BLW14_RS19305'
1
'MTSDRAYHHGDLRRAVLTAALDVIRTEGPAALSLRDLARRAGVSHAAPAHHFKDRTGLLTAVAAEGYALFADTLAAA

'MINSNASHDDAEIAVAAVRAGAEVVRARYGQRLTRIDKGAGDFATDADVAAEEAILDVIRAARPGDAVHGEEGGRRGADDAARQWLVDPLCGTLNYAVGHMLVAVNVALRGGPAAVADPFTGEVFFTDGENAWVRGDEGDTPLAPTAATKLVDVNLDAPFPSAPGFRAVDLLAHPGFVARFRPRVVSTTLALAWVATGSRAAYVTDGGDLTGSVHFAAGIALCRDAGCVVTGVDGAPVGQAGRGLLVAADAETHGLLLSMIRGRG' 'DN051_RS36610'
1
'MHDRSIRWGILATGPMAAAFTEDLRTIPGADVVAVGSRSQDSAQAFADRFAIPRAYGSWQELADDPDIDVVYVATPHAHHLAAATVCLEGGKAVLCEKPFALSRAQTESMIATAGDCSLFLMEGMWTFVNPLVRRAQEMIGDGMIGEVVSVRAEFSSRAPVVPGSRLRDPAAGGGALLDIGTYPVSFAHLFLGAPDHVSAWAHLNDAGVDESTAMVLGYDGGAMAVLSCSLAFGSANGAVVYGTEGRIEFPSAFYNPRQLVLHRDGREPRVVEAEPQLGNGYGFQAEEVMSCLREKKTESALVPLRTSLDVMSTLDRVRELVGVRYPGE' 'DN051_RS36615'
2
'MAAGHDLSPSEAPAALSFPPSFTWGTATAAYQIEGAATLDGRTPSIWDTYSRTPGKVRNGDTGDTATDHYHRWREDVAIMADLGVGAYRFSIAWPRVQPTGRGPSVQKGLDFYRKLADELLEKNIQPVATLYHWDLPQELEDAGGWPERVTAERFAEYAGLAAEALGDRVRTWITLNEPWCSAFLGYSSGVHAPGRTDPVAALRAAHHLNLGHGKAVQALRANLPSDAQVSVTLNIHHVRPFTDDAQDVDAARRIDALANRVFTGPMLQGAYPEDLLRDTASLTDWSFVQDGDLKEIRQPLDFLGVNYYTPTLVSGGASGTSHGSDGHGKSEHSPWPAADDVTFHLPPGSTTAMGWAVDPTGL

WP_105970816.1
["'CW359_RS17115'", "'CW359_RS17120'", "'CW359_RS17125'", "'CW359_RS17130'", "'CW359_RS17135'", "'CW359_RS17140'", "'CW359_RS17145'", "'CW359_RS17150'", "'CW359_RS17155'", "'CW359_RS17160'", "'CW359_RS17165'", "'CW359_RS17170'", "'CW359_RS17175'", "'CW359_RS17180'", "'CW359_RS17185'", "'CW359_RS17190'", "'CW359_RS17195'", "'CW359_RS17200'", "'CW359_RS17205'", "'CW359_RS17210'", "'CW359_RS17215'", "'CW359_RS17220'", "'CW359_RS17225'", 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test']
0
'MRAAGRPLSRTLTRALPVTPAVVLLVLFLAGPIAYCAYIAFTDLQLTGQAESSFIGFENFRTAFKDKAFLNAVWLTLVFTVLSSLLGQNTLGLALAALMQRASKPVRTLVGGIVITAWVLPEVVAGFLLYAFFRREGTLNAILAWLHLPSQNWLFTLPILAVSFANVWRGTAFSMLVYSAALNEIPKEITEAAEMDGAGGWRRMWHITLPMIRRSIGTNLMLNTLQTLSVFGLIWVMTRGGPGNRSQTLPLFMYEQAFQKSMIGYGTAVALLLLVVGSLFSVVYMRLLRTEV' 'CW359_RS17115'
1
'MLVRPTAARTTTPLSLFVAAALTLAAGSLTACGGGSGSDPDTVRISFKQSTDNSVKVMDTYLADIKKQFENENPGKKAELVPIKAPDSEYYTKVQQMLRSPKTAPDLVYEDTFLINSDITSGYLKPLDAYLAKWPAWNQFIDTAKTAARAE

...

8
'METGTSQREDHQQEAAARRRKELLEAADRVVLRDGPEASMNAIAAEAGITKPILYRHFGDKGGLYRALAVRHTDALLASLRKALDAPAPDRRGRVAATLDTYLAAIEARPQVYRFLMHPADQGQQQEQGFDVGHHSAPLLRRMGDELAKVIADRVELGPGGEEVARIWGHGIVGMMHAAGDWWLRERPCSRERLVHHLTDLLWGRLALVDDRAGAPGLF' 'EEJ42_RS17690'
9
'MRNGAIPGSRGTVRPLRLLGDQALRAPCEEVSDFDAALARLVEDLFATMYAAGGVGLAANQIGVGLRVFVYDCPDDEDRRHLGHVVNPRLAEADGVTVRGTEGCLSLPGIESGTPRFDRAVVEGVTVTGEPVRVEGSGFFARCLQHECDHLDGGLFLDRLGGLRRRRVLWAARRAPWARGRA' 'EEJ42_RS17695'
10
'MAGNSEPLSPRAKLAVTAGRAAAAVSKAAGRGSGSVIGGKVALRLDPDLLSRLAHHLDVILVSATNGKTTTTRLIAEALRAAGPVVSNALGANMPAGITSALAGGSDARYGVIEVDEKYLAGVARDTEPKAIALLNLSRDQLDRAAETRMLAEKWREGLAGTKATVIANADDPLIVWAASSSPNVVWVAAGQEWKDDAWSCPACGGVLQRPGDDWVCGECGFRRPVPSWALNGEYVLDPHGAAWPIHLQLPGRANKANAATSAAVAATFGVPPQVALERMYQVQAVAGRYDVVTFQERELRLLLAKNPAGWLETFSLIDPPPTPVILSVNARGADGTDTSWLWDVDYTRLAGHPICVIGDRKLDLAVRLEVAGLDFRVCADADEAVRISPPGRIEVIANYTAFQDLRRRVGN' 'EEJ42_RS17700'
11
'MRSTSQNGLRLVWVYPDLLSTYGDQGNVLVVERRARQRGLDVSRLDVRSDQQIPTSGDIYLIGGGEDRPQRLAAERLMRDGGLNRAVANGAIVFSVCAGYQILGHEFVNDLGQRQQGLG

9
'MTATEDSAAPQQQLPPPGRRRHRPEPAPGARRSRRAAPAPKPRKTKTVRTPTVLQMEAVECGAASLAMVLAHFGRHVPLEELRIACGVSRDGSRASNLLKAARSYGLQAKGMQMEPSALAEVQAPAILFWEFNHYVVYDGTSRRFGRRGVRINDPDKGRRFVPTEDFDTSFTGVALVFEPGEDFRKGGRKPGVLGAVPARMRGTTGTLLAALLASLLLVAVGAAVPALSRTYIDMFLIGNQTSLLGPLFASMAAMVALTAVLTGLQQANLLRGRIISSTLTSARFLRHLLRLPVTFFAQRSPADLVQRLQSNDAVAETLARDLAAAGVDGIVVILYAFLLWTYDPQLTVIGVGIALLNVVAMRIVIRLRATHTQKLRADTARLTNTSYTGLQLIETMKATGGENGYFRRWAGQHATTLEVQQRLGVPSAALAVVAPTLATLNSALILWIGGLRAVEGHISIGLLVAFQALVTRFTAPITRLNGVAGRIQDFAADVARLKDVESFPVDTLYSRPEPDADTRRLKGHVTLEDITFGYSPLDKPLLTGFSLAVGPGRQVALVGGSGSGKSTVSRLISGLYSPWEGTIRIDGQRLEDLSRSALAASVSFVDQDIFLFEGTVRDNVALWDPSIPDDAVITALQDAALYDDVIARRPDGIHSRVEQDGRNFSGGQRQRLEIARALVRRPSILVLDEVTSALDAQTEQTIMDNLRRRGCACVVIAHRLSTVRDSDEIVVLDHGVVVERGRHENLVAAGGPYAELVKEH' 'BLW51_RS32545'
10
'MPPPAVVGPGATDAVTQALGGLGTPVDCTGLRSVPLEGPHVLWLVTGGSLDLFAVDAVEEGHWHFLGRLEAGTLLLGPVAGPHHTLLGRPSQDCLLRRIELRELPRYDYGEYGDTGSIPQYGTQDGYGYTAHDGQGEALSALEHAFALGTARSLGVLFEAPLDGRPADEAVADDDILWMPVPPGSVQYGASYSAEAAGDLLVDPDLWQQMVNQQ

'MTKKTRIRLARVAAGAVIAAGASMTAAGAASASETENCLLGLLCSSEAPTTPPPLPTPTSTGIPGEEEPSVPPITEEPPTDEPTEPEEPTEDPGNGNGNGNGNGNGNGNGQGENGGGGNNTDPKGGSGNDAVTQEEGSSSLTDTGSSVPAGTNTAAQGGDELAETGAAETTFLLVGAATMIAGGIGFRLLPRMMGGRGGAAA' 'E0500_RS03635'
25
'MSVVDVSEELKSLSSTMESIEAVLDLDKLRADIAVLEEQAAAPSLWDNPDEAQKITSKLSHLQAEVRKAETLRGRIDDLGVLFEMAEEEDDPDTRAEAESELAAVKKALDEMEVRTLLSGEYDAREALVNIRAEAGGVDAADFAEKLQRMYLRWAEQHGYKTEIYETSYAEEAGIKSTTFAVQIPYAYGTLSVEQGTHRLVRISPFDNQGRRQTSFAGVEVLPVVEQSDHVEIDESELRIDVYRSSGPGGQGVNTTDSAVRITHLPTGIVVSCQNERSQIQNKATAMNVLQAKLLERRRQEEQARMDALKGDGGNSWGNQMRSYVLHPYQMVKDLRTEHEVGNPEAVFNGEIDGFLEAGIRWRKQQEK' 'E0500_RS03640'
26
'MTRKIGSRYTANQILGRGSAGTVWLGEGPEGPVAIKLLREDLASDQELVGRFVQERTALLGLEHRNVVSVRDLVVDGNDLALVMDLVRGTDLRTRLDRERRMAPEAAVAIVADVADALAAAHSAGVVHRDVKPENVLLDMQGPLGPGGAHPALLTDFGVAKLIDSPRRTRATKIIGTPDYLAPEIVEGLPPRAAVDIYALATVLYELLAGFTPFGGGHPGAVLRRHVTETVVPLPGIPEELWQLLVQCLAKAPASRLRASELGARLREQLPSLAGMPPLDVDEPDAEPQEAHEEETEAAAPRERERVRRGAVPLVPGAKPDSNRDTHTSMRVPGPDELAGGARGTARVPRAAGAPRPGSARHRATTRRRRITLGAAAVVLLAAVG

WP_099940479.1
["'CLW12_RS14395'", "'CLW12_RS14400'", "'CLW12_RS14405'", "'CLW12_RS14415'", "'CLW12_RS14420'", "'CLW12_RS14425'", "'CLW12_RS14430'", "'CLW12_RS14435'", "'CLW12_RS14440'", "'CLW12_RS14445'", "'CLW12_RS14450'", "'CLW12_RS14455'", "'CLW12_RS14460'", "'CLW12_RS14465'", "'CLW12_RS14470'", "'CLW12_RS14475'", "'CLW12_RS14480'", "'CLW12_RS14485'", "'CLW12_RS14490'", "'CLW12_RS14495'", "'CLW12_RS14500'", "'CLW12_RS14505'", "'CLW12_RS14510'", "'CLW12_RS14515'", "'CLW12_RS14520'", "'CLW12_RS14525'", "'CLW12_RS14530'", "'CLW12_RS14535'", 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test', 'test']
0
'MKKITLGGEGLEVSRLGLGCMGMSGGYTGAGTDDSGSIATIHRAMELGVTYFDTAEIYGPYTNEELLAKAFAGHRDEVVIATKFGQINHLVPEENGQPVLGLNGTPANVRRSVEGSLRRLNTDYIDLYYQHRIDPETPIEDTVGTLSELIEEGKIRHYGLSEAAPATIRRAHAVHPVTALQTEYSLWTRDPEAEVLPTVRELGIGFVPYSPLGRGFLTGTIRSLDQLDADDWRRSNPRFEGDNLEANIRIVEQVDDVARQLGATPAQVALAWLLAQGDDIAPIPGTRRAANLEQNVAADALGLSAEQLEQLSEVAAPVGDRYADMSRINQ' 'CLW12_RS14395'
1
'MRVVSLVPSLTEAVAVTV

IndexError: list index out of range

# Scann through folder and save all files that dont contain blast hits

In [18]:
import os
import glob
string1= "Sequences producing significant alignments:"
path = '/home/friederike/ncbi-blast-2.11.0+/bin/allp450ncbi_strep_ecoli_positivesover60out/'
for filename in glob.glob(os.path.join(path, '*.fasta')):
    
        file1 = open(filename, "r") 
        readfile = file1.read()

        if string1 in readfile:
            pass
        else:  
             print (filename)
        

/home/friederike/ncbi-blast-2.11.0+/bin/allp450ncbi_strep_ecoli_positivesover60out/WP_153542803.1_1774216491.fasta
/home/friederike/ncbi-blast-2.11.0+/bin/allp450ncbi_strep_ecoli_positivesover60out/WP_093590071.1_1225596427.fasta
/home/friederike/ncbi-blast-2.11.0+/bin/allp450ncbi_strep_ecoli_positivesover60out/WP_078893581.1_759552000.fasta
/home/friederike/ncbi-blast-2.11.0+/bin/allp450ncbi_strep_ecoli_positivesover60out/WP_010984950.1_1152364355.fasta
/home/friederike/ncbi-blast-2.11.0+/bin/allp450ncbi_strep_ecoli_positivesover60out/WP_097238906.1_1254335166.fasta
/home/friederike/ncbi-blast-2.11.0+/bin/allp450ncbi_strep_ecoli_positivesover60out/WP_168130939.1_1906668074.fasta
/home/friederike/ncbi-blast-2.11.0+/bin/allp450ncbi_strep_ecoli_positivesover60out/WP_003958577.1_1661329808.fasta
/home/friederike/ncbi-blast-2.11.0+/bin/allp450ncbi_strep_ecoli_positivesover60out/WP_056799034.1_948143065.fasta
/home/friederike/ncbi-blast-2.11.0+/bin/allp450ncbi_strep_ecoli_positivesover60out

# Convert all gbk to fasta in directory

In [6]:
from Bio import SeqIO
import os
import glob

path = '/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/'
for filename in glob.glob(os.path.join(path, '*.gbk')):
 
    
        file1 = open(filename, "r") 
        
        print (file1)
       

        faa_filename=filename[:-4]+".fasta"
        output_handle = open(faa_filename, "w")

        for seq_record in SeqIO.parse(file1, "genbank") :
            print ("t")
           
            for seq_feature in seq_record.features :
                
                if seq_feature.type=="CDS" :
                    assert len(seq_feature.qualifiers['translation'])==1
                    try: idf=seq_feature.qualifiers['protein_id'][0]
                    except:
                        try: idf=seq_feature.qualifiers['locus_tag'][0]
                        except:idf="no_id"
                    output_handle.write(">%s from %s\n%s\n" % (
                           idf,
                           seq_record.name,
                           seq_feature.qualifiers['translation'][0]))

        output_handle.close()
        file1.close()


<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/BGC0000027.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/BGC0000682.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/phormidolide.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/saprolmycin_e.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Bost

t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/BGC0001205.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/aureothin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/erythromycin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/prodigiosin_4.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Bos

t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/filipin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/spore_pigment_2.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/BGC0000030.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/maduropeptin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Bos

t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/napyradiomycin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/neocarzinostatin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/BGC0000156.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/BGC0001143.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederi

t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/BGC0000098.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/elansolid.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/aranciamycin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/azicemicin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston

t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/divergolide.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/migrastatin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/BGC0000070.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/pactamycin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Bosto

t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/pederin_2.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/aculeximycin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/BGC0001246.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/neocarzilin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Bosto

t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/BGC0000959.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/cosmomycin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/red_pigment.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/erdacin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/Al

t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/arimetamycin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/kijanimicin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/lomaiviticin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederike/Boston/AllisonsProgramm/Natural-product-function-master/Matrices for all NP/polyketides/polyketidesantismash/tetracenomycin.gbk' mode='r' encoding='UTF-8'>
t
<_io.TextIOWrapper name='/home/friederike/Dokumente/Diplom/Work Friederik